In [ ]:
%pip install -Uq bertopic

     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 103.9/103.9 KB 3.7 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 662.4/662.4 KB 17.4 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 5.2/5.2 MB 62.6 MB/s eta 0:00:00
  Installing build dependencies ... done
  Getting requirements to build wheel ... done
  Preparing metadata (pyproject.toml) ... done
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 86.0/86.0 KB 10.4 MB/s eta 0:00:00
  Preparing metadata (setup.py) ... done
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 88.2/88.2 KB 10.8 MB/s eta 0:00:00
  Preparing metadata (setup.py) ... done
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 5.8/5.8 MB 83.9 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 1.3/1.3 MB 64.9 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 182.4/182.4 KB 20.5 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 1.1/1.1 MB 64.2 MB/s eta 0:00:00
  Preparing metadata (setup.py) ... done
     ━━━━━━━━━━━━━━━━

In [ ]:
import pandas as pd
import nltk
import string
import umap
import hdbscan
import bertopic
import sentence_transformers
import sklearn
import numpy as np

from bertopic import BERTopic
from sentence_transformers import SentenceTransformer
from sklearn.feature_extraction.text import CountVectorizer
from nltk.corpus import stopwords
from nltk.stem.snowball import SnowballStemmer
from umap import UMAP
from hdbscan import HDBSCAN



nltk.download('stopwords', quiet=True)
nltk.download('punkt', quiet=True)


True

In [69]:
normalization = 1
eliminate_hip_hop = 0

In [70]:
df = pd.read_csv('tcc_ceds_music.csv')

print(df.shape, "\n", df.columns)

#display(df)

(28372, 31) 
 Index(['Unnamed: 0', 'artist_name', 'track_name', 'release_date', 'genre',
       'lyrics', 'len', 'dating', 'violence', 'world/life', 'night/time',
       'shake the audience', 'family/gospel', 'romantic', 'communication',
       'obscene', 'music', 'movement/places', 'light/visual perceptions',
       'family/spiritual', 'like/girls', 'sadness', 'feelings', 'danceability',
       'loudness', 'acousticness', 'instrumentalness', 'valence', 'energy',
       'topic', 'age'],
      dtype='object')


In [71]:
# df_usage = df.sample(8000)
# df_usage.reset_index(inplace = True,drop = True)

df_usage = df.copy()

#display(df_usage)

In [72]:
if eliminate_hip_hop == 1:
  genre_dict = {}
  for i in df_usage['genre']:
    if i in genre_dict:
      genre_dict[i] += 1
    else:
      genre_dict[i] = 1

  for i in genre_dict:
    print(i, genre_dict[i])

  df_without_hiphop = df_usage[df_usage.genre != "hip hop"]
  df_usage = df_without_hiphop.copy()
  print("\n")

if normalization == 1:
  genre_dict = {}
  for i in df_usage['genre']:
    if i in genre_dict:
      genre_dict[i] += 1
    else:
      genre_dict[i] = 1

  for i in genre_dict:
    print(i, genre_dict[i])

  min_value = min(genre_dict.values())
  print(min_value)

  new_df = df_usage.groupby('genre').sample(min_value)

  new_df = new_df.sample(frac = 1)
  new_df.reset_index(inplace = True,drop = True)

  display(new_df)

  df_usage = new_df.copy()

pop 7042
country 5445
blues 4604
jazz 3845
reggae 2498
rock 4034
hip hop 904
904


Unnamed: 0          artist_name  \
0          45558          peter green   
1          53676           larkin poe   
2          70527         carl perkins   
3          47748         marvin sease   
4          71910           pink floyd   
...          ...                  ...   
6323       60993        roberta flack   
6324       58651       the blackbyrds   
6325       64926         prince far i   
6326       14473  my chemical romance   
6327       81340           positive k   

                                        track_name  release_date    genre  \
0                                bullet in the sky          1981    blues   
1                               john the revelator          2017    blues   
2                                 that's all right          1958     rock   
3                                    it's too late          1991    blues   
4                                           seamus          1971     rock   
...                                            ...           ...      ...   
6323                   tonight i celebrate my love          2006     jazz   
6324                                  do it, fluid          1989     jazz   
6325                              shuffle and deal          1989   reggae   
6326                     this is the best day ever          2002      pop   
6327  i'm not havin’ it (re-recorded / remastered)          2009  hip hop   

                                                 lyrics  len    dating  \
0     bullet load pain bullet carry bullet come stra...   42  0.001698   
1     tell write revelator tell write revelator tell...  103  0.000721   
2     right right right mama mama tell papa tell mes...   36  0.075058   
3     come time life realise take trust years lie co...  195  0.000384   
4     kitchen outside kitchen hound outside know sin...   11  0.006579   
...                                                 ...  ...       ...   
6323  tonight celebrate natural thing tonight gonna ...   53  0.001224   
6324  like party like party like party like party wa...   75  0.000835   
6325  dress robe clothe continent stitch paint face ...   84  0.000849   
6326  backdrop gear scalpels hour go ticktock bang m...   59  0.001144   
6327  want culture mind cheese want hear music origi...   90  0.001096   

      violence  world/life  ...   sadness  feelings  danceability  loudness  \
0     0.361885    0.001698  ...  0.001698  0.001698      0.609011  0.678179   
1     0.000721    0.000721  ...  0.000721  0.000721      0.328496  0.791837   
2     0.001504    0.001504  ...  0.001504  0.033139      0.578685  0.627003   
3     0.246209    0.325712  ...  0.100757  0.023571      0.690242  0.559547   
4     0.411648    0.006579  ...  0.243753  0.006579      0.513701  0.326770   
...        ...         ...  ...       ...       ...           ...       ...   
6323  0.001224    0.001224  ...  0.001224  0.001224      0.444384  0.607697   
6324  0.000835    0.000835  ...  0.000835  0.000835      0.671829  0.580801   
6325  0.000849    0.146166  ...  0.000849  0.058980      0.851619  0.617183   
6326  0.057050    0.001144  ...  0.612027  0.001144      0.234268  0.760736   
6327  0.107283    0.001096  ...  0.001096  0.042320      0.809379  0.629234   

      acousticness  instrumentalness   valence    energy       topic       age  
0         0.348393          0.379555  0.598104  0.699690    violence  0.557143  
1         0.905622          0.000005  0.241550  0.553540       music  0.042857  
2         0.646586          0.000010  0.600165  0.673663  night/time  0.885714  
3         0.720883          0.000000  0.346661  0.353333  world/life  0.414286  
4         0.810241          0.110324  0.344600  0.086958    violence  0.700000  
...            ...               ...       ...       ...         ...       ...  
6323      0.776104          0.000035  0.113768  0.289267  night/time  0.200000  
6324      0.252007          0.005213  0.897980  0.529515     obscene  0.442857  
6325      0.088453   

In [73]:
eng_stopword_list = nltk.corpus.stopwords.words('english')
stemmer = SnowballStemmer(language='english')

for lyric_counter in range(len(df_usage["lyrics"])):
  
  temp_lowercase_tokenize_doc = nltk.word_tokenize(
      df_usage["lyrics"][lyric_counter].lower())

  for stopword in eng_stopword_list:
    if stopword in temp_lowercase_tokenize_doc:
      temp_list = []
      for elem in temp_lowercase_tokenize_doc:
        if elem != stopword:
          temp_list.append(elem)
      temp_lowercase_tokenize_doc = temp_list
   
  punctuations = string.punctuation
  for symbol in punctuations:
    temp_list = []
    for elem in temp_lowercase_tokenize_doc: 
      if symbol != elem:
        if symbol in elem:
          elem = elem.replace(symbol, '')
        temp_list.append(elem)
    temp_lowercase_tokenize_doc = temp_list 

  temp_list = []
  for elem in temp_lowercase_tokenize_doc:
    temp_list.append(stemmer.stem(elem))
  temp_lowercase_tokenize_doc = temp_list

  temp_doc = ' '.join(temp_lowercase_tokenize_doc)
  df_usage["lyrics"][lyric_counter] = temp_doc

  if lyric_counter % 1000 == 0:
    print(lyric_counter)

#display(df_usage)

0
1000
2000
3000
4000
5000
6000


In [74]:
genre_dict = {}
for i in df_usage['genre']:
  if i in genre_dict:
    genre_dict[i] += 1
  else:
    genre_dict[i] = 1

for i in genre_dict:
  print(i, genre_dict[i])

blues 904
rock 904
pop 904
jazz 904
reggae 904
hip hop 904
country 904


In [75]:
umap_model = UMAP(n_neighbors=30, n_components=2, min_dist=0.01)
hdbscan_model = HDBSCAN(min_cluster_size=50, min_samples=2, prediction_data=True, cluster_selection_method="leaf")

embedding_model = SentenceTransformer('all-MiniLM-L6-v2')

model = BERTopic(
    embedding_model=embedding_model,
    umap_model=umap_model,
    language='english',
    #calculate_probabilities=True,
    verbose=True,
    hdbscan_model = hdbscan_model
)


#Comment out next line for loading
topics, probs = model.fit_transform(df_usage['lyrics'])

Batches:   0%|          | 0/198 [00:00<?, ?it/s]

2023-01-06 14:12:44,744 - BERTopic - Transformed documents to Embeddings
2023-01-06 14:13:07,156 - BERTopic - Reduced dimensionality
2023-01-06 14:13:07,317 - BERTopic - Clustered reduced embeddings


In [76]:
print(model.get_topic_info(), "\n")

    Topic  Count                             Name
0      -1   3080           -1_like_know_time_come
1       0    156         0_blood_dead_kill_beckon
2       1    155            1_hold_good_like_uhoh
3       2    151              2_like_shit_fuck_na
4       3    138           3_home_long_babi_right
5       4    134           4_leav_minut_fall_feel
6       5    118           5_leav_readi_time_home
7       6    113          6_song_radio_sing_music
8       7    111         7_song_hear_sing_tonight
9       8    105           8_life_world_live_ugli
10      9    103         9_polic_crash_chim_zilla
11     10    100         10_dream_away_promis_day
12     11    100     11_suffer_lunaci_save_betray
13     12     93     12_parti_tonight_drinkin_gon
14     13     92         13_time_bling_late_forev
15     14     92          14_like_money_diva_know
16     15     89         15_wall_head_static_side
17     16     89          16_hurt_heart_babi_know
18     17     84         17_money_yiggi_fame_bald


In [77]:
print(model.get_topic_info(), "\n")

fig = model.visualize_documents(df_usage['lyrics'])
fig.write_html("Graph1_1.html")

fig

    Topic  Count                             Name
0      -1   3080           -1_like_know_time_come
1       0    156         0_blood_dead_kill_beckon
2       1    155            1_hold_good_like_uhoh
3       2    151              2_like_shit_fuck_na
4       3    138           3_home_long_babi_right
5       4    134           4_leav_minut_fall_feel
6       5    118           5_leav_readi_time_home
7       6    113          6_song_radio_sing_music
8       7    111         7_song_hear_sing_tonight
9       8    105           8_life_world_live_ugli
10      9    103         9_polic_crash_chim_zilla
11     10    100         10_dream_away_promis_day
12     11    100     11_suffer_lunaci_save_betray
13     12     93     12_parti_tonight_drinkin_gon
14     13     92         13_time_bling_late_forev
15     14     92          14_like_money_diva_know
16     15     89         15_wall_head_static_side
17     16     89          16_hurt_heart_babi_know
18     17     84         17_money_yiggi_fame_bald


In [78]:
model.save("Model1_1")

In [79]:
model = model.load("Model1_1")
print(model.get_topic_info(), "\n")

    Topic  Count                             Name
0      -1   3080           -1_like_know_time_come
1       0    156         0_blood_dead_kill_beckon
2       1    155            1_hold_good_like_uhoh
3       2    151              2_like_shit_fuck_na
4       3    138           3_home_long_babi_right
5       4    134           4_leav_minut_fall_feel
6       5    118           5_leav_readi_time_home
7       6    113          6_song_radio_sing_music
8       7    111         7_song_hear_sing_tonight
9       8    105           8_life_world_live_ugli
10      9    103         9_polic_crash_chim_zilla
11     10    100         10_dream_away_promis_day
12     11    100     11_suffer_lunaci_save_betray
13     12     93     12_parti_tonight_drinkin_gon
14     13     92         13_time_bling_late_forev
15     14     92          14_like_money_diva_know
16     15     89         15_wall_head_static_side
17     16     89          16_hurt_heart_babi_know
18     17     84         17_money_yiggi_fame_bald


In [80]:
print(model.get_topic_info())

size_param = 25

model.reduce_topics(nr_topics=size_param, docs=df_usage["lyrics"])

print(model.get_topic_info())

    Topic  Count                             Name
0      -1   3080           -1_like_know_time_come
1       0    156         0_blood_dead_kill_beckon
2       1    155            1_hold_good_like_uhoh
3       2    151              2_like_shit_fuck_na
4       3    138           3_home_long_babi_right
5       4    134           4_leav_minut_fall_feel
6       5    118           5_leav_readi_time_home
7       6    113          6_song_radio_sing_music
8       7    111         7_song_hear_sing_tonight
9       8    105           8_life_world_live_ugli
10      9    103         9_polic_crash_chim_zilla
11     10    100         10_dream_away_promis_day
12     11    100     11_suffer_lunaci_save_betray
13     12     93     12_parti_tonight_drinkin_gon
14     13     92         13_time_bling_late_forev
15     14     92          14_like_money_diva_know
16     15     89         15_wall_head_static_side
17     16     89          16_hurt_heart_babi_know
18     17     84         17_money_yiggi_fame_bald


2023-01-06 14:21:53,421 - BERTopic - Reduced number of topics from 37 to 26


    Topic  Count                          Name
0      -1   3461        -1_like_know_time_come
1       0    208           0_like_shit_na_fuck
2       1    208       1_nigga_bitch_shit_fuck
3       2    173     2_dream_away_tonight_time
4       3    156      3_blood_dead_kill_beckon
5       4    155         4_hold_good_like_come
6       5    138        5_home_long_babi_right
7       6    134        6_leav_minut_feel_away
8       7    123       7_heart_break_babi_good
9       8    118        8_leav_readi_time_home
10      9    113       9_song_radio_sing_music
11     10    111     10_song_hear_sing_tonight
12     11    105       11_life_world_live_ugli
13     12    103     12_polic_crash_zilla_chim
14     13    100  13_suffer_lunaci_save_betray
15     14     93  14_parti_tonight_gon_drinkin
16     15     92     15_like_money_know_better
17     16     92       16_time_bling_know_late
18     17     89      17_wall_head_static_side
19     18     89       18_hurt_heart_know_babi
20     19    

In [81]:
print(model.get_topic_info(), "\n")

fig = model.visualize_documents(df_usage['lyrics'])
fig.write_html("Graph1_2.html")

fig

    Topic  Count                          Name
0      -1   3461        -1_like_know_time_come
1       0    208           0_like_shit_na_fuck
2       1    208       1_nigga_bitch_shit_fuck
3       2    173     2_dream_away_tonight_time
4       3    156      3_blood_dead_kill_beckon
5       4    155         4_hold_good_like_come
6       5    138        5_home_long_babi_right
7       6    134        6_leav_minut_feel_away
8       7    123       7_heart_break_babi_good
9       8    118        8_leav_readi_time_home
10      9    113       9_song_radio_sing_music
11     10    111     10_song_hear_sing_tonight
12     11    105       11_life_world_live_ugli
13     12    103     12_polic_crash_zilla_chim
14     13    100  13_suffer_lunaci_save_betray
15     14     93  14_parti_tonight_gon_drinkin
16     15     92     15_like_money_know_better
17     16     92       16_time_bling_know_late
18     17     89      17_wall_head_static_side
19     18     89       18_hurt_heart_know_babi
20     19    

In [82]:
model.save("Model1_2")

In [89]:
model = model.load("Model1_2")
print(model.get_topic_info(), "\n")

    Topic  Count                          Name
0      -1   3461        -1_like_know_time_come
1       0    208           0_like_shit_na_fuck
2       1    208       1_nigga_bitch_shit_fuck
3       2    173     2_dream_away_tonight_time
4       3    156      3_blood_dead_kill_beckon
5       4    155         4_hold_good_like_come
6       5    138        5_home_long_babi_right
7       6    134        6_leav_minut_feel_away
8       7    123       7_heart_break_babi_good
9       8    118        8_leav_readi_time_home
10      9    113       9_song_radio_sing_music
11     10    111     10_song_hear_sing_tonight
12     11    105       11_life_world_live_ugli
13     12    103     12_polic_crash_zilla_chim
14     13    100  13_suffer_lunaci_save_betray
15     14     93  14_parti_tonight_gon_drinkin
16     15     92     15_like_money_know_better
17     16     92       16_time_bling_know_late
18     17     89      17_wall_head_static_side
19     18     89       18_hurt_heart_know_babi
20     19    

In [84]:
new_topics = model.reduce_outliers(documents=df_usage["lyrics"], topics=model.topics_)

model.update_topics(docs=df_usage["lyrics"], topics=new_topics)

print(model.get_topic_info(), "\n")

100%|██████████| 4/4 [00:02<00:00,  1.43it/s]


    Topic  Count                             Name
0       0    721              0_like_fuck_shit_na
1       1    378          1_nigga_bitch_fuck_shit
2       2    361         2_dream_away_day_tonight
3       3    310          3_blood_dead_kill_death
4       4    288            4_hold_good_line_come
5       5    297             5_home_long_babi_gon
6       6    303            6_feel_leav_fall_away
7       7    330          7_heart_break_know_babi
8       8    225         8_leav_readi_knee_goodby
9       9    223          9_song_sing_music_radio
10     10    189        10_hear_tonight_walk_blue
11     11    463        11_life_live_world_believ
12     12    134        12_aliv_polic_shoot_crash
13     13    184  13_save_suffer_believ_arrowhead
14     14    133   14_parti_friday_everybodi_like
15     15    171         15_better_like_real_pump
16     16    232           16_time_late_long_know
17     17    195          17_head_wall_hand_grind
18     18    168        18_hurt_strong_heart_feel


In [85]:
print(model.get_topic_info(), "\n")

fig = model.visualize_documents(df_usage['lyrics'])
fig.write_html("Graph1_3.html")

fig

    Topic  Count                             Name
0       0    721              0_like_fuck_shit_na
1       1    378          1_nigga_bitch_fuck_shit
2       2    361         2_dream_away_day_tonight
3       3    310          3_blood_dead_kill_death
4       4    288            4_hold_good_line_come
5       5    297             5_home_long_babi_gon
6       6    303            6_feel_leav_fall_away
7       7    330          7_heart_break_know_babi
8       8    225         8_leav_readi_knee_goodby
9       9    223          9_song_sing_music_radio
10     10    189        10_hear_tonight_walk_blue
11     11    463        11_life_live_world_believ
12     12    134        12_aliv_polic_shoot_crash
13     13    184  13_save_suffer_believ_arrowhead
14     14    133   14_parti_friday_everybodi_like
15     15    171         15_better_like_real_pump
16     16    232           16_time_late_long_know
17     17    195          17_head_wall_hand_grind
18     18    168        18_hurt_strong_heart_feel


In [86]:
model.save("Model1_3")

In [87]:
model = model.load("Model1_3")
print(model.get_topic_info(), "\n")

    Topic  Count                             Name
0       0    721              0_like_fuck_shit_na
1       1    378          1_nigga_bitch_fuck_shit
2       2    361         2_dream_away_day_tonight
3       3    310          3_blood_dead_kill_death
4       4    288            4_hold_good_line_come
5       5    297             5_home_long_babi_gon
6       6    303            6_feel_leav_fall_away
7       7    330          7_heart_break_know_babi
8       8    225         8_leav_readi_knee_goodby
9       9    223          9_song_sing_music_radio
10     10    189        10_hear_tonight_walk_blue
11     11    463        11_life_live_world_believ
12     12    134        12_aliv_polic_shoot_crash
13     13    184  13_save_suffer_believ_arrowhead
14     14    133   14_parti_friday_everybodi_like
15     15    171         15_better_like_real_pump
16     16    232           16_time_late_long_know
17     17    195          17_head_wall_hand_grind
18     18    168        18_hurt_strong_heart_feel


In [90]:
print(model.get_topic_info(), "\n")

topic_dict = model.get_topics()
topic_genre_index_zip = list(zip(model.topics_, df_usage["genre"]))

genre_list = df_usage['genre'].unique()
frequency_arr = np.zeros((len(topic_dict),len(genre_list)))

genre_dict = {}
for index in range(len(genre_list)):
  genre_dict[genre_list[index]] = index

for elem in genre_dict:
  print(elem, genre_dict[elem])

for index in range(len(topic_genre_index_zip)):
  frequency_arr[topic_genre_index_zip[index][0]][genre_dict[topic_genre_index_zip[index][1]]] += 1

print("\n")

output = pd.DataFrame(frequency_arr, columns = genre_list)

print(output)

    Topic  Count                          Name
0      -1   3461        -1_like_know_time_come
1       0    208           0_like_shit_na_fuck
2       1    208       1_nigga_bitch_shit_fuck
3       2    173     2_dream_away_tonight_time
4       3    156      3_blood_dead_kill_beckon
5       4    155         4_hold_good_like_come
6       5    138        5_home_long_babi_right
7       6    134        6_leav_minut_feel_away
8       7    123       7_heart_break_babi_good
9       8    118        8_leav_readi_time_home
10      9    113       9_song_radio_sing_music
11     10    111     10_song_hear_sing_tonight
12     11    105       11_life_world_live_ugli
13     12    103     12_polic_crash_zilla_chim
14     13    100  13_suffer_lunaci_save_betray
15     14     93  14_parti_tonight_gon_drinkin
16     15     92     15_like_money_know_better
17     16     92       16_time_bling_know_late
18     17     89      17_wall_head_static_side
19     18     89       18_hurt_heart_know_babi
20     19    

In [91]:
eng_stopword_list = nltk.corpus.stopwords.words('english')
stemmer = SnowballStemmer(language='english')

for lyric_counter in range(len(df_usage["track_name"])):
  
  temp_lowercase_tokenize_doc = nltk.word_tokenize(
      df_usage["track_name"][lyric_counter].lower())
   
  punctuations = string.punctuation
  for symbol in punctuations:
    temp_list = []
    for elem in temp_lowercase_tokenize_doc: 
      if symbol != elem:
        if symbol in elem:
          elem = elem.replace(symbol, '')
        temp_list.append(elem)
    temp_lowercase_tokenize_doc = temp_list 

  temp_doc = ' '.join(temp_lowercase_tokenize_doc)
  df_usage["track_name"][lyric_counter] = temp_doc

  if lyric_counter % 1000 == 0:
    print(lyric_counter)


0
1000
2000
3000
4000
5000
6000


In [92]:
print(model.get_topics())

topic_dict2 = model.get_topics()

topic_dict2_pre_process = {}

for key in topic_dict2:
  topic_str = ""
  for elem in topic_dict2[key]:
    topic_str += (elem[0] + " ")

  topic_str = topic_str.rstrip(topic_str[-1])
  topic_dict2_pre_process[key] = topic_str

topic_title_genre_index_zip = list(zip(model.topics_, df_usage["track_name"], df_usage["genre"]))

topictitle_genre_arr = []
for elem in topic_title_genre_index_zip:
  if elem[0] != -1:
    topictitle_str = topic_dict2_pre_process[elem[0]] + " " + elem[1]
    topictitle_genre_arr.append((elem[2], topictitle_str))

output_test = pd.DataFrame(topictitle_genre_arr, columns = ["genre", "topictitle"])

display(output_test)



{-1: [('like', 0.019783668893827665), ('know', 0.018271678256989027), ('time', 0.016955600024352806), ('come', 0.016676032881983417), ('feel', 0.015238425094219575), ('life', 0.014166470370874306), ('yeah', 0.0141154909525577), ('away', 0.013185368968628371), ('na', 0.013178926558236506), ('caus', 0.013170204737486799)], 0: [('like', 0.03060006610760738), ('shit', 0.02454315964102699), ('na', 0.020611484366514204), ('fuck', 0.02038126814539593), ('caus', 0.018078556971187622), ('bitch', 0.01790518894092752), ('know', 0.016543514353352943), ('got', 0.01648147856738691), ('wan', 0.0161085340696848), ('nigga', 0.015830556001417653)], 1: [('nigga', 0.11576797000020773), ('bitch', 0.04625489481791989), ('shit', 0.036743885273345246), ('fuck', 0.03390263768305404), ('like', 0.028943222587774868), ('yeah', 0.025403294237809834), ('know', 0.020282114411972137), ('niggaz', 0.019865917615656332), ('lyric', 0.01968356373046671), ('commerci', 0.019279554315283002)], 2: [('dream', 0.064557628332468

genre                                         topictitle
0       blues  blood dead kill beckon fear like get eye anti ...
1       blues  long faster fall tell eye away lose mind know ...
2        rock  polic crash zilla chim simmer jingl go hand mo...
3        jazz  fool heart away break yesterday fall tear lie ...
4       blues  parti tonight gon drinkin boy go ring gettin n...
...       ...                                                ...
2862    blues  leav readi time home know stand long knee na j...
2863  country  polic crash zilla chim simmer jingl go hand mo...
2864     jazz  song hear sing tonight bell thee babi nearer w...
2865     jazz  money yiggi fame bald good know better boog su...
2866   reggae  hold good like come call right go grave uhoh c...

[2867 rows x 2 columns]